<a href="https://colab.research.google.com/github/wongzw/IS4242_Group_4/blob/4-knn-model/knn_model_mp.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [15]:
import pickle
import joblib
import cv2
import os
import re
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_predict
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import classification_report, accuracy_score
from sklearn.metrics import roc_auc_score
from google.colab import drive
from tqdm import tqdm
from PIL import Image

!pip install mediapipe

import tensorflow as tf
import mediapipe as mp


from google.colab import drive
drive.mount('/content/drive', force_remount = True)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Mounted at /content/drive


### Attempt with Mediapipe

In [16]:
folder_name = f"/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/data" # Update with Folder Details

In [17]:
image_paths = os.listdir(folder_name)
img_list = []
label_list = []
txt = 'abcdefghiklmnopqrstuvwxy'

for i in tqdm(range(len(os.listdir(folder_name)))):
  filename = os.listdir(folder_name)[i]
  if filename.endswith(('.jpg','.png')):
      label_name = re.split(r'[-_]', filename)[0].lower()
      if label_name not in txt:
        continue
      label_list.append(label_name)
      img = cv2.imread(os.path.join(folder_name, filename))
      img = cv2.resize(img, (28,28))
      img_array = np.array(img)
      
      img_list.append(img_array)


100%|██████████| 1221/1221 [01:54<00:00, 10.64it/s]


Train-Test Split

In [18]:
X = np.array(img_list)
y = np.array(label_list)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify = y)

In [19]:
output_dir = f"/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/"

joblib.dump(X, output_dir+'X_knn_mp.pkl')
joblib.dump(y, output_dir+'y_knn_mp.pkl')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/y_knn_mp.pkl']

Data Augmentation

In [20]:
import albumentations as A

transform = A.Compose([
    A.RandomBrightnessContrast(),
    A.Affine(scale=[0.8,1.2],translate_percent=0.05, shear=0.2, keep_ratio=True, p=0.5),
    A.Rotate(limit=10)
])

In [21]:
augmented_X = []
augmented_y = []
for i in range(len(X_train)):
  for j in (range(10)):
      transformed = transform(image=X_train[i])
      augmented_X.append(transformed['image'])
      augmented_y.append(y_train[i])

augmented_X = np.array(augmented_X)
augmented_y = np.array(augmented_y)
X_train = np.concatenate([X_train,augmented_X])
y_train = np.concatenate([y_train,augmented_y])

Generate datsset of hand points

In [22]:
mediapipe_drawing = mp.solutions.drawing_utils
mediapipe_hands = mp.solutions.hands

In [23]:
image_paths = os.listdir(folder_name)
X_train_data = []
y_train_label = []

with mediapipe_hands.Hands(static_image_mode = True, max_num_hands = 2, min_detection_confidence = 0.5) as hands: 
    for i in tqdm(range(len(X_train))):
        results = hands.process(cv2.cvtColor(cv2.flip(X_train[i],1), cv2.COLOR_BGR2RGB))
        try:
            # Extract Hand landmarks
            for hand_landmark in results.multi_hand_landmarks:
                right_hand = hand_landmark.landmark
            right_hand_row = list(np.array([[landmark.x, landmark.y] for landmark in right_hand]).flatten())
            # Concate rows
            row = right_hand_row

            # Extract the label from the image filename (e.g. "A.jpg")
            label = y_train[i]
            
            X_train_data.append(row) 
            y_train_label.append(label)
            print(row, label)

        except AttributeError as e:
            print(f"LOGGING: No hands detected for X_train-{i}")

        except Exception as e:
            pass


  0%|          | 4/7183 [00:00<07:01, 17.03it/s]

[0.5673426389694214, 0.2354227751493454, 0.47277840971946716, 0.2764406204223633, 0.4546845555305481, 0.389759361743927, 0.48346593976020813, 0.4733627438545227, 0.5227476954460144, 0.5220065116882324, 0.4860565662384033, 0.45670393109321594, 0.48383963108062744, 0.5708500742912292, 0.4852903187274933, 0.6440932750701904, 0.49189072847366333, 0.6966425776481628, 0.5627148747444153, 0.4592650830745697, 0.5550837516784668, 0.5816835761070251, 0.5546086430549622, 0.6636790633201599, 0.5614247918128967, 0.7237369418144226, 0.6327486634254456, 0.4375363886356354, 0.6420041918754578, 0.5058156847953796, 0.6289246082305908, 0.4720350205898285, 0.6174284219741821, 0.4330296218395233, 0.6887216567993164, 0.4007774591445923, 0.6909523010253906, 0.4495057463645935, 0.678485095500946, 0.4230811893939972, 0.6686513423919678, 0.3936348259449005] h
[0.48592936992645264, 0.9014410376548767, 0.39029258489608765, 0.8302247524261475, 0.3697955906391144, 0.7024679183959961, 0.4626189172267914, 0.599800109

  0%|          | 10/7183 [00:00<06:24, 18.67it/s]

[0.2977364957332611, 0.23680752515792847, 0.37130799889564514, 0.2504006624221802, 0.41476112604141235, 0.3170675039291382, 0.39633721113204956, 0.3730842173099518, 0.3580769896507263, 0.3904941976070404, 0.30086928606033325, 0.31051337718963623, 0.27443844079971313, 0.3465614914894104, 0.27766314148902893, 0.37756600975990295, 0.27915525436401367, 0.40201762318611145, 0.26344946026802063, 0.34385982155799866, 0.2605831027030945, 0.42761504650115967, 0.29379215836524963, 0.4807230234146118, 0.3120017945766449, 0.5116804838180542, 0.24723801016807556, 0.36675649881362915, 0.2661324441432953, 0.44746100902557373, 0.30596014857292175, 0.44834017753601074, 0.32084745168685913, 0.43516436219215393, 0.24209266901016235, 0.3749602138996124, 0.2707889676094055, 0.4399215579032898, 0.304360568523407, 0.445435106754303, 0.3210572600364685, 0.4359974265098572] t
[0.5288901329040527, 0.8387202620506287, 0.4247654378414154, 0.8005401492118835, 0.3550739288330078, 0.7334737181663513, 0.3674982190132

  0%|          | 14/7183 [00:00<07:07, 16.77it/s]

...

[0.678958535194397, 0.4650130867958069, 0.6001142859458923, 0.4397420883178711, 0.5106732845306396, 0.42798200249671936, 0.4483678340911865, 0.43073758482933044, 0.42580705881118774, 0.4332845211029053, 0.33226412534713745, 0.4335421323776245, 0.30085888504981995, 0.4719941020011902, 0.3836430013179779, 0.48666638135910034, 0.44616585969924927, 0.4760981500148773, 0.3308466076850891, 0.4510510563850403, 0.3083573281764984, 0.47922471165657043, 0.40058404207229614, 0.4917161166667938, 0.4755844473838806, 0.4822068214416504, 0.34531304240226746, 0.46195533871650696, 0.34326136112213135, 0.48692038655281067, 0.4229671061038971, 0.49277636408805847, 0.48738083243370056, 0.48627403378486633, 0.3725353181362152, 0.46929436922073364, 0.37836968898773193, 0.49079641699790955, 0.4350978434085846, 0.49833589792251587, 0.4796622097492218, 0.49428585171699524] m
[0.5779499411582947, 0.5025303959846497, 0.5051262378692627, 0.5014749765396118, 0.42292582988739014, 0.5111579895019531, 0.3743231594562

100%|█████████▉| 7182/7183 [08:07<00:00, 13.76it/s]

[0.695354700088501, 0.4961214065551758, 0.6051088571548462, 0.46726077795028687, 0.5026006698608398, 0.4484892785549164, 0.4290006160736084, 0.45185285806655884, 0.4019315540790558, 0.45495373010635376, 0.3559609055519104, 0.4372091293334961, 0.2897493839263916, 0.45128127932548523, 0.36906301975250244, 0.46935388445854187, 0.431401789188385, 0.46396300196647644, 0.36147475242614746, 0.443871408700943, 0.2970105707645416, 0.4496796429157257, 0.3876193165779114, 0.47080275416374207, 0.45596352219581604, 0.467822402715683, 0.3813619017601013, 0.442813515663147, 0.34130343794822693, 0.44926130771636963, 0.4157153367996216, 0.4671630859375, 0.47421449422836304, 0.4686599671840668, 0.41426077485084534, 0.43897444009780884, 0.38770920038223267, 0.4435766339302063, 0.43944844603538513, 0.4613534212112427, 0.4823472797870636, 0.46436232328414917] m
[0.6575842499732971, 0.4884639084339142, 0.6035610437393188, 0.4560548663139343, 0.5148115754127502, 0.4323485791683197, 0.45297008752822876, 0.423

100%|██████████| 7183/7183 [08:07<00:00, 14.73it/s]

[0.5229880809783936, 0.537886917591095, 0.4439534544944763, 0.5549170970916748, 0.3634081780910492, 0.5576318502426147, 0.32236430048942566, 0.5528936982154846, 0.3121214210987091, 0.5449202060699463, 0.3286948800086975, 0.4628662168979645, 0.2735384702682495, 0.4842303693294525, 0.3060912489891052, 0.5276355743408203, 0.33099856972694397, 0.5360412001609802, 0.388494074344635, 0.44350722432136536, 0.34643930196762085, 0.49244385957717896, 0.37306010723114014, 0.5313249826431274, 0.3957012891769409, 0.5348466634750366, 0.45231497287750244, 0.4373312294483185, 0.42772936820983887, 0.4934747815132141, 0.4502355456352234, 0.5303137898445129, 0.46798190474510193, 0.5400845408439636, 0.5138648152351379, 0.4402424693107605, 0.5009974837303162, 0.4822123646736145, 0.5116466283798218, 0.5146293044090271, 0.5239415764808655, 0.5240160226821899] m


In [24]:
joblib.dump(X_train_data, output_dir+'knn_mp_train_data.pkl')
joblib.dump(y_train_label, output_dir+'knn_mp_train_label.pkl')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/knn_mp_train_label.pkl']

In [25]:
image_paths = os.listdir(folder_name)
X_test_data = []
y_test_label = []

with mediapipe_hands.Hands(static_image_mode = True, max_num_hands = 2, min_detection_confidence = 0.5) as hands: 
    for i in tqdm(range(len(X_test))):
        results = hands.process(cv2.cvtColor(cv2.flip(X_train[i],1), cv2.COLOR_BGR2RGB))
        try:
            # Extract Hand landmarks
            for hand_landmark in results.multi_hand_landmarks:
                right_hand = hand_landmark.landmark
            right_hand_row = list(np.array([[landmark.x, landmark.y] for landmark in right_hand]).flatten())
            # Concate rows
            row = right_hand_row

            # Extract the label from the image filename (e.g. "A.jpg")
            label = y_test[i]
                
            X_test_data.append(row) 
            y_test_label.append(label)
            print(row, label)

        except AttributeError as e:
            print(f"LOGGING: No hands detected for X_test-{i}")

        except Exception as e:
            pass

  2%|▏         | 3/164 [00:00<00:14, 10.98it/s]

[0.5673426389694214, 0.2354227751493454, 0.47277840971946716, 0.2764406204223633, 0.4546845555305481, 0.389759361743927, 0.48346593976020813, 0.4733627438545227, 0.5227476954460144, 0.5220065116882324, 0.4860565662384033, 0.45670393109321594, 0.48383963108062744, 0.5708500742912292, 0.4852903187274933, 0.6440932750701904, 0.49189072847366333, 0.6966425776481628, 0.5627148747444153, 0.4592650830745697, 0.5550837516784668, 0.5816835761070251, 0.5546086430549622, 0.6636790633201599, 0.5614247918128967, 0.7237369418144226, 0.6327486634254456, 0.4375363886356354, 0.6420041918754578, 0.5058156847953796, 0.6289246082305908, 0.4720350205898285, 0.6174284219741821, 0.4330296218395233, 0.6887216567993164, 0.4007774591445923, 0.6909523010253906, 0.4495057463645935, 0.678485095500946, 0.4230811893939972, 0.6686513423919678, 0.3936348259449005] l
[0.48592936992645264, 0.9014410376548767, 0.39029258489608765, 0.8302247524261475, 0.3697955906391144, 0.7024679183959961, 0.4626189172267914, 0.599800109

  4%|▍         | 7/164 [00:00<00:11, 13.22it/s]

[0.36791935563087463, 0.9316091537475586, 0.28377851843833923, 0.8468841314315796, 0.24471908807754517, 0.7082346081733704, 0.25438201427459717, 0.6005826592445374, 0.2980092763900757, 0.543547511100769, 0.38040584325790405, 0.5957204699516296, 0.40802568197250366, 0.5038174390792847, 0.3861345946788788, 0.47452497482299805, 0.37470221519470215, 0.49389806389808655, 0.43680262565612793, 0.6146463751792908, 0.369430810213089, 0.5643349289894104, 0.31195902824401855, 0.626762866973877, 0.3065236806869507, 0.6845418214797974, 0.47870224714279175, 0.6526634097099304, 0.3964267075061798, 0.6134478449821472, 0.3416256606578827, 0.6687338352203369, 0.34206244349479675, 0.7151468992233276, 0.5098549127578735, 0.7028740048408508, 0.41674166917800903, 0.6700873374938965, 0.36610159277915955, 0.7083860635757446, 0.3647160530090332, 0.748045027256012] q
[0.2977364957332611, 0.23680752515792847, 0.37130799889564514, 0.2504006624221802, 0.41476112604141235, 0.3170675039291382, 0.39633721113204956, 0

  5%|▌         | 9/164 [00:00<00:11, 13.41it/s]

...

 96%|█████████▋| 158/164 [00:09<00:00, 18.68it/s]

[0.5908961892127991, 0.663161039352417, 0.44340914487838745, 0.6399055123329163, 0.3066798448562622, 0.4980577230453491, 0.2775324583053589, 0.36841878294944763, 0.2744487524032593, 0.27164125442504883, 0.3856853246688843, 0.338837593793869, 0.3578993082046509, 0.24170376360416412, 0.37590929865837097, 0.31955188512802124, 0.3879343867301941, 0.41182640194892883, 0.5066539645195007, 0.33138933777809143, 0.47429680824279785, 0.24227303266525269, 0.4826470911502838, 0.35771697759628296, 0.48795270919799805, 0.46068644523620605, 0.6273535490036011, 0.3506911098957062, 0.5876155495643616, 0.2881452441215515, 0.5818957686424255, 0.40664586424827576, 0.5827980041503906, 0.5016719102859497, 0.745537519454956, 0.39017531275749207, 0.7038884162902832, 0.31803447008132935, 0.6822662353515625, 0.39972782135009766, 0.6837033033370972, 0.47427845001220703] c
[0.5175839066505432, 0.9187496304512024, 0.3803217113018036, 0.8203287124633789, 0.3208194375038147, 0.666114091873169, 0.3448423445224762, 0.

 99%|█████████▉| 163/164 [00:09<00:00, 20.03it/s]

[0.7130686044692993, 0.46658188104629517, 0.6689344644546509, 0.626998245716095, 0.498354434967041, 0.7506215572357178, 0.33673423528671265, 0.7768846750259399, 0.22324970364570618, 0.7634681463241577, 0.30334973335266113, 0.683475911617279, 0.18274129927158356, 0.6564594507217407, 0.31221210956573486, 0.6415877938270569, 0.3842639625072479, 0.6442044973373413, 0.30187129974365234, 0.574784517288208, 0.19453033804893494, 0.5412970781326294, 0.34944233298301697, 0.544211745262146, 0.39786675572395325, 0.5603926181793213, 0.31576982140541077, 0.471763014793396, 0.228504478931427, 0.44004660844802856, 0.37098366022109985, 0.4521275758743286, 0.416946679353714, 0.4669274091720581, 0.3458327353000641, 0.37116310000419617, 0.2609540522098541, 0.35199594497680664, 0.3675616979598999, 0.36957108974456787, 0.416702002286911, 0.3840652108192444] a
[0.5729838609695435, 0.6048052906990051, 0.5061458945274353, 0.5836935639381409, 0.448833703994751, 0.5395584106445312, 0.4006912112236023, 0.50895446

100%|██████████| 164/164 [00:09<00:00, 17.50it/s]


In [26]:
joblib.dump(X_test_data, output_dir+'knn_mp_test_data.pkl')
joblib.dump(y_test_label, output_dir+'knn_mp_test_label.pkl')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/knn_mp_test_label.pkl']

In [27]:
X_train = np.array(X_train_data)
X_test = np.array(X_test_data)
print(X_train.shape)
print(X_test.shape)

(5424, 42)
(133, 42)


In [28]:
y_train = np.array(y_train_label)
y_test = np.array(y_test_label)
print(y_train.shape)
print(y_test.shape)

(5424,)
(133,)


Model Training and Testing

In [29]:
k = 3 # Choose the number of neighbors
classifier_mp = KNeighborsClassifier(n_neighbors=k)
classifier_mp.fit(X_train, y_train)

joblib.dump(classifier_mp, output_dir+'knn_model_mp.joblib')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/knn_model_mp.joblib']

In [30]:
y_mp_pred = classifier_mp.predict(X_test)
accuracy = accuracy_score(y_test, y_mp_pred)
print("Accuracy:", accuracy)

classifiction_report = classification_report(y_test, y_mp_pred)
print("Classification Report:", classifiction_report)

Accuracy: 0.03007518796992481
Classification Report:               precision    recall  f1-score   support

           a       0.17      0.17      0.17         6
           b       0.00      0.00      0.00         6
           c       0.00      0.00      0.00         5
           d       0.20      0.20      0.20         5
           e       0.00      0.00      0.00         5
           f       0.00      0.00      0.00         5
           g       0.00      0.00      0.00         5
           h       0.20      0.29      0.24         7
           i       0.00      0.00      0.00         4
           k       0.00      0.00      0.00         2
           l       0.00      0.00      0.00         6
           m       0.00      0.00      0.00         6
           n       0.00      0.00      0.00         6
           o       0.00      0.00      0.00         4
           p       0.00      0.00      0.00         4
           q       0.00      0.00      0.00         6
           r       0.00     

In [31]:
y_mp_score = classifier_mp.predict_proba(X_test)

In [32]:
macro_roc_auc_ovr_tuned = roc_auc_score(
    y_test,
    y_mp_score,
    multi_class="ovr",
    average="macro",
)

print(f"Macro-averaged One-vs-Rest ROC AUC score:\n{macro_roc_auc_ovr_tuned}")

Macro-averaged One-vs-Rest ROC AUC score:
0.4914418216766876


#### Hyperparameter Tuning

In [33]:
grid_params = {'n_neighbors': [3, 5, 7],
               'weights': ['uniform', 'distance'],
               'algorithm':['kd_tree', 'auto'],
               'p': [1, 2],
               'metric' : ['minkowski','euclidean','manhattan']}

gs_mp = GridSearchCV(KNeighborsClassifier(), grid_params,scoring='accuracy', verbose = 3, cv=3, n_jobs = -1)

In [34]:
g_res_mp = gs_mp.fit(X_train, y_train)

Fitting 3 folds for each of 72 candidates, totalling 216 fits


In [35]:
print(g_res_mp.best_score_)
print(g_res_mp.best_params_)

0.6898967551622418
{'algorithm': 'kd_tree', 'metric': 'minkowski', 'n_neighbors': 3, 'p': 2, 'weights': 'distance'}


Evaluating Tunned Model

In [36]:
knn_mp_tuned = KNeighborsClassifier(n_neighbors = g_res_mp.best_params_['n_neighbors'], weights = g_res_mp.best_params_['weights'],algorithm = g_res_mp.best_params_['algorithm'],metric = g_res_mp.best_params_['metric'],p = g_res_mp.best_params_['p'])
knn_mp_tuned.fit(X_train, y_train)

KNeighborsClassifier(algorithm='kd_tree', n_neighbors=3, weights='distance')

In [37]:
joblib.dump(knn_mp_tuned, output_dir+'knn_model_mp_tuned.joblib')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/knn_model_mp_tuned.joblib']

In [38]:
y_pred_mp_tuned = knn_mp_tuned.predict(X_test)
print(classification_report(y_test, y_pred_mp_tuned))
print(f"Accuracy Score: {accuracy_score(y_test, y_pred_mp_tuned)}")

              precision    recall  f1-score   support

           a       0.20      0.17      0.18         6
           b       0.00      0.00      0.00         6
           c       0.00      0.00      0.00         5
           d       0.20      0.20      0.20         5
           e       0.00      0.00      0.00         5
           f       0.00      0.00      0.00         5
           g       0.00      0.00      0.00         5
           h       0.20      0.29      0.24         7
           i       0.00      0.00      0.00         4
           k       0.00      0.00      0.00         2
           l       0.00      0.00      0.00         6
           m       0.00      0.00      0.00         6
           n       0.00      0.00      0.00         6
           o       0.00      0.00      0.00         4
           p       0.00      0.00      0.00         4
           q       0.00      0.00      0.00         6
           r       0.00      0.00      0.00         5
           s       0.00    

In [39]:
y_score_mp_tuned = knn_mp_tuned.predict_proba(X_test)

macro_roc_auc_ovr_tuned = roc_auc_score(
    y_test,
    y_score_mp_tuned,
    multi_class="ovr",
    average="macro",
)

print(f"Macro-averaged One-vs-Rest ROC AUC score:\n{macro_roc_auc_ovr_tuned:.2f}")

Macro-averaged One-vs-Rest ROC AUC score:
0.49


#### Cross Validation

In [40]:
output_dir = f"/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/"
X_train = joblib.load(output_dir+'knn_mp_train_data.pkl')
X_test = joblib.load(output_dir+'knn_mp_test_data.pkl')
y_train = joblib.load(output_dir+'knn_mp_train_label.pkl')
y_test = joblib.load(output_dir+'knn_mp_test_label.pkl')

In [41]:
kfold = KFold(n_splits=5, shuffle = True,  random_state = 42)
classifier_cv = KNeighborsClassifier(n_neighbors=3)
X_cv = np.concatenate([X_train,X_test])
y_cv = np.concatenate([y_train,y_test])

In [42]:
y_pred_classifier_cv = cross_val_predict(classifier_cv, X_cv, y_cv, cv=kfold)

In [43]:
print(classification_report(y_cv, y_pred_classifier_cv))
print(f"Accuracy Score: {accuracy_score(y_cv, y_pred_classifier_cv)}")

y_pred_classifier_cv_score = cross_val_predict(classifier_cv, X_cv, y_cv, cv=kfold, method='predict_proba')
auc_scores = roc_auc_score(y_cv, y_pred_classifier_cv_score, multi_class='ovr')

print("AUC scores: ", auc_scores)


              precision    recall  f1-score   support

           a       0.88      0.92      0.90       231
           b       0.87      0.91      0.89       247
           c       0.87      0.94      0.90       216
           d       0.85      0.85      0.85       225
           e       0.83      0.83      0.83       244
           f       0.95      0.92      0.93       261
           g       0.86      0.93      0.89       201
           h       0.85      0.86      0.86       169
           i       0.88      0.85      0.87       235
           k       0.86      0.90      0.88       222
           l       0.94      0.94      0.94       247
           m       0.73      0.73      0.73       171
           n       0.83      0.79      0.81       219
           o       0.85      0.86      0.86       202
           p       0.91      0.83      0.87       153
           q       0.91      0.87      0.89       191
           r       0.80      0.84      0.82       264
           s       0.80    

#### Hyperparameter Tuning

In [44]:
import multiprocessing
grid_params = {'n_neighbors': [3, 5, 7, 9],
               'weights': ['uniform', 'distance'],
               'algorithm':['kd_tree', 'auto'],
               'p': [1, 2],
               'metric' : ['minkowski','euclidean','manhattan']}

kf = KFold(n_splits=5, shuffle=True, random_state=42)

gs_cv = GridSearchCV(KNeighborsClassifier(), grid_params,scoring='accuracy', verbose = 3, cv=kf, n_jobs = -1)

In [45]:
g_cv_res = gs_cv.fit(X_cv, y_cv)

Fitting 5 folds for each of 96 candidates, totalling 480 fits


In [46]:
print(g_cv_res.best_score_)
print(g_cv_res.best_params_)

0.8747515039273711
{'algorithm': 'auto', 'metric': 'minkowski', 'n_neighbors': 3, 'p': 2, 'weights': 'distance'}


Evaluating Tunned Model

In [47]:
classifier_cv_tuned = KNeighborsClassifier(n_neighbors = g_cv_res.best_params_['n_neighbors'], weights = g_cv_res.best_params_['weights'],algorithm = g_cv_res.best_params_['algorithm'],metric = g_cv_res.best_params_['metric'],p = g_cv_res.best_params_['p'])
y_pred_tuned_cv = cross_val_predict(classifier_cv_tuned, X_cv, y_cv, cv=kfold)

In [50]:
joblib.dump(y_pred_tuned_cv, output_dir+'knn.joblib')

['/content/drive/MyDrive/4. NUS/Studies/Y4S2/IS4242/IS4242/dump/knn.joblib']

In [49]:
print(classification_report(y_cv, y_pred_tuned_cv))
print(f"Accuracy Score: {accuracy_score(y_cv, y_pred_tuned_cv)}")

y_pred_classifier_tuned_cv_score = cross_val_predict(classifier_cv_tuned, X_cv, y_cv, cv=kfold, method='predict_proba')
auc_scores = roc_auc_score(y_cv, y_pred_classifier_tuned_cv_score, multi_class='ovr')

print("AUC scores: ", auc_scores)


              precision    recall  f1-score   support

           a       0.92      0.91      0.92       231
           b       0.88      0.90      0.89       247
           c       0.89      0.93      0.91       216
           d       0.91      0.86      0.88       225
           e       0.89      0.84      0.87       244
           f       0.95      0.93      0.94       261
           g       0.87      0.90      0.89       201
           h       0.85      0.88      0.86       169
           i       0.90      0.86      0.88       235
           k       0.88      0.88      0.88       222
           l       0.92      0.92      0.92       247
           m       0.75      0.77      0.76       171
           n       0.84      0.79      0.82       219
           o       0.85      0.86      0.86       202
           p       0.91      0.82      0.87       153
           q       0.87      0.91      0.89       191
           r       0.84      0.84      0.84       264
           s       0.81    